In [1]:
%matplotlib inline
#----------------------------------------------------------------------
#------------------------- IMPORT LIBRARIES ---------------------------
import json # reading geojson files
import matplotlib.pyplot as plt # plotting data
import folium
import pandas as pd
import numpy as np
from unidecode import unidecode

ImportError: No module named 'unidecode'

In [20]:
# Data
murders_df = pd.read_csv("./data/asesinatos.csv", sep=";")
slaughters_df = pd.read_csv("./data/masacres.csv", sep=";")

In [21]:
murders_df.head(2)

Día Mes     Año Departamento        Municipio Lugar de Ocurrencia  \
0   6   1  1981.0    Santander  Barrancabermeja                 NaN   
1   7   1  1981.0        Huila        Algeciras                 NaN   

          Tipo de Implicado (1)         Tipo de Implicado (2) Nº Víctimas  \
0  Grupo Armado No Identificado  Grupo Armado No Identificado           1   
1          Grupos Paramilitares          Grupos Paramilitares           2   

                                              Fuente Unnamed: 10  
0  Itinerario de la Represión Oficial y Militar e...         NaN  
1  Itinerario de la Represión Oficial y Militar e...         NaN

In [5]:
slaughters_df.head(2)

Día Mes     Año Departamento    Municipio Lugar de Ocurrencia  \
0   2  10  1980.0      Caquetá  Puerto Rico   Vereda El Topacio   
1  24  10  1980.0       Arauca         Tame       IPD La Arabia   

                  Tipo de Implicado  Nº Víctimas  \
0              Grupos Paramilitares            5   
1  Fuerza Pública-Ejército Nacional            5   

                                              Fuente Unnamed: 9  
0                     Enterrar y Callar Pp. 109 CPDH        NaN  
1  Enterrar y Callar Pp. 89 Boletín de Prensa CPD...        NaN

In [24]:
murders_df["Tipo de Implicado (1)"].unique()

array(['Grupo Armado No Identificado', 'Grupos Paramilitares',
       'Fuerza Pública', 'Desconocidos', ' Grupos Paramilitares',
       'Guerrilla  ', 'Fuerza Pública-Grupos Paramilitares', 'Guerrilla',
       'Otros Grupos Armados', 'Guerrilla-ELN', nan], dtype=object)

In [25]:
slaughters_df["Tipo de Implicado"].unique()

array(['Grupos Paramilitares', 'Fuerza Pública-Ejército Nacional',
       'Guerrilla-FARC ', 'Guerrilla-ELN ', 'Grupo Armado No Identificado',
       'Fuerza Pública-Policía Nacional',
       'Fuerza Pública-Grupos Paramilitares', 'Guerrilla-EPL ',
       'Guerrilla No Identificada',
       'Guerrilla Conjunta-Quintin Lame y M-19',
       'Guerrilla-Ricardo Franco ', 'Guerrilla-Quintin Lame ',
       'Agente Extranjero-Guardia Nacional Venezolana',
       'Guerrilla-Milicias Populares',
       'Otro Grupo Armado-Comandos Populares',
       'Guerrilla Conjunta-FARC y EPL', 'Otro Grupo Armado-Convivir',
       'Guerrilla Conjunta-FARC y ELN', 'Guerrilla-ERP ',
       'Fuerza Pública-Ejército Nacional/Policía Nacional',
       'Fuerza Pública-Ejército Nacional/Infantería de Marina', nan], dtype=object)

In [30]:
def category(x):
    if "Guerrilla" in x:
        return "Guerrilla"
    elif ("Paramilitares" in x) or ("Pública" in x):
        return "Paramilitares - Estado"
    else:
        return np.NaN

In [33]:
#Clean - Geo
murders_df = murders_df[~murders_df["Departamento"].isnull()]
slaughters_df = slaughters_df[~slaughters_df["Departamento"].isnull()]
murders_df = murders_df[~murders_df["Nº Víctimas"].isnull()]
slaughters_df = slaughters_df[~slaughters_df["Nº Víctimas"].isnull()]
murders_df["Departamento"] = murders_df["Departamento"].apply(lambda x:x.strip())
murders_df["Nº Víctimas"] = murders_df["Nº Víctimas"].apply(lambda x:x.replace("´1","1"))
murders_df["Departamento"] = murders_df["Departamento"].apply(lambda x:x.replace("Choco","Chocó"))
slaughters_df["Departamento"] = slaughters_df["Departamento"].apply(lambda x:x.replace("Quindio","Quindío"))
murders_df["Departamento"] = murders_df["Departamento"].apply(lambda x:x.replace("meta","Meta"))
murders_df["Departamento"] = murders_df["Departamento"].apply(lambda x:x.replace("César","Cesar"))
slaughters_df["Departamento"] = slaughters_df["Departamento"].apply(lambda x:x.strip())
departaments_mu = set(murders_df["Departamento"].unique())
departaments_sl = set(slaughters_df["Departamento"].unique())
weird_set = departaments_mu - departaments_sl - set(["Vaupés", "San Andrés Isla"]) | set(["Exterior"])
murders_df = murders_df[~murders_df["Departamento"].isin(weird_set)]
weird_set = departaments_sl - departaments_mu - set(["Guainía"]) | set(["Exterior"])
slaughters_df = slaughters_df[~slaughters_df["Departamento"].isin(weird_set)]
#Clean - Type
murders_df["implicado"] = murders_df["Tipo de Implicado (1)"].apply(category)
slaughters_df["implicado"] = slaughters_df["Tipo de Implicado"].apply(category)

In [34]:
#Filter
murders_df = murders_df[["Departamento","Nº Víctimas","implicado"]]
murders_df.columns = ["depto","count","implicado"]
murders_df["count"] = murders_df["count"].astype(int)
slaughters_df = slaughters_df[["Departamento","Nº Víctimas","implicado"]]
slaughters_df.columns = ["depto","count","implicado"]

In [35]:
#Join
print(len(murders_df))
print(len(slaughters_df))
df = murders_df.append(slaughters_df)
print(len(df))

16304
1976
18280


In [36]:
df.head(2)

depto  count               implicado
0  Santander      1                     NaN
1      Huila      2  Paramilitares - Estado

In [37]:
#Names
df["depto"] = df["depto"].apply(lambda x:unidecode(x).upper())
df["depto"] = df["depto"].apply(lambda x:x.replace("DISTRITO CAPITAL","SANTAFE DE BOGOTA D.C"))
df["depto"] = df["depto"].apply(lambda x:x.replace("SAN ANDRES ISLA","ARCHIPIELAGO DE SAN ANDRES PROVIDENCIA Y SANTA CATALINA"))
df["depto"] = df["depto"].apply(lambda x:x.replace("NARINO","NARIÑO"))

In [39]:
#Division
df_para = df[df["implicado"] == "Paramilitares - Estado"]

df_guer = df[df["implicado"] == "Guerrilla"]

In [40]:
#Group
df_sum_para = df_para.groupby("depto").sum()
df_sum_guer = df_guer.groupby("depto").sum()

In [59]:
df_sum_para

count
depto                                                    
ANTIOQUIA                                            4921
ARAUCA                                                350
ARCHIPIELAGO DE SAN ANDRES PROVIDENCIA Y SANTA ...      1
ATLANTICO                                             177
BOLIVAR                                              1016
BOYACA                                                278
CALDAS                                                361
CAQUETA                                               255
CASANARE                                              211
CAUCA                                                 787
CESAR                                                1186
CHOCO                                                 321
CORDOBA                                               635
CUNDINAMARCA                                          265
GUAVIARE                                              134
HUILA                                                 296
LA GUAJIRA                                            310
MAGDALENA                                             962
META                                                 1003
NARIÑO                                                344
NORTE DE SANTANDER                                   1294
PUTUMAYO                                              265
QUINDIO                                                54
RISARALDA                                             215
SANTAFE DE BOGOTA D.C                                 214
SANTANDER                                            1737
SUCRE                                                 332
TOLIMA                                                434
VALLE DEL CAUCA                                      1003
VAUPES                                                  2
VICHADA                                                25

In [60]:
df_sum_guer

count
depto                       
ANTIOQUIA               1662
ARAUCA                   223
ATLANTICO                 14
BOLIVAR                  274
BOYACA                    72
CALDAS                   104
CAQUETA                  164
CASANARE                  55
CAUCA                    396
CESAR                    204
CHOCO                    123
CORDOBA                  198
CUNDINAMARCA             121
GUAINIA                    4
GUAVIARE                  71
HUILA                    197
LA GUAJIRA                37
MAGDALENA                126
META                     192
NARIÑO                   121
NORTE DE SANTANDER       398
PUTUMAYO                  63
QUINDIO                   28
RISARALDA                 57
SANTAFE DE BOGOTA D.C     14
SANTANDER                444
SUCRE                    112
TOLIMA                   322
VALLE DEL CAUCA          161
VAUPES                     2
VICHADA                    8

In [52]:
por = (df_sum_para)/(df_sum_para + df_sum_guer)*100

In [62]:
df_sum_count = por.reset_index()
df_sum_count
df_sum_para = df_sum_para.reset_index()
df_sum_guer = df_sum_guer.reset_index()

In [14]:
import branca.colormap as cm
cm.linear

In [58]:
geo_str = json.dumps(json.load(open("colombia.geojson", 'r')))
threshold_scale = np.linspace(df_sum_count['count'].min(),
                              df_sum_count['count'].max(), 6, dtype=int).tolist()

state_geo = r'colombia.geojson'

mapa = folium.Map(location=[4.7110, -74.0721],
                  tiles="Mapbox Bright",
                  zoom_start=5)

mapa.choropleth(geo_data=state_geo, data=df_sum_count,
             columns=['depto', 'count'],
             key_on='properties.NOMBRE_DPT',
             fill_color='YlGn', fill_opacity=0.7, line_opacity=0.2,
             threshold_scale = threshold_scale,
             legend_name='Percentage of victims of targeted killings and massacres due to paramilitary groups and public force')

mapa

In [64]:
geo_str = json.dumps(json.load(open("colombia.geojson", 'r')))
threshold_scale = np.linspace(df_sum_para['count'].min(),
                              df_sum_para['count'].max(), 6, dtype=int).tolist()

state_geo = r'colombia.geojson'
mapa = folium.Map(location=[4.7110, -74.0721],
                  tiles="Mapbox Bright",
                  zoom_start=5)

mapa.choropleth(geo_data=state_geo, data=df_sum_para,
             columns=['depto', 'count'],
             key_on='properties.NOMBRE_DPT',
             fill_color='YlGn', fill_opacity=0.7, line_opacity=0.2,
             threshold_scale = threshold_scale,
             legend_name='Percentage of victims of targeted killings and massacres due to paramilitary groups and public force')

mapa

In [65]:
geo_str = json.dumps(json.load(open("colombia.geojson", 'r')))
threshold_scale = np.linspace(df_sum_guer['count'].min(),
                              df_sum_guer['count'].max(), 6, dtype=int).tolist()

state_geo = r'colombia.geojson'

mapa = folium.Map(location=[4.7110, -74.0721],
                  tiles="Mapbox Bright",
                  zoom_start=5)

mapa.choropleth(geo_data=state_geo, data=df_sum_guer,
             columns=['depto', 'count'],
             key_on='properties.NOMBRE_DPT',
             fill_color='YlGn', fill_opacity=0.7, line_opacity=0.2,
             threshold_scale = threshold_scale,
             legend_name='Percentage of victims of targeted killings and massacres due to paramilitary groups and public force')

mapa